In [1]:
import pandas as pd
import numpy as np
import os
from pathlib import Path
import pickle
from multiprocessing import Pool
from runpy import run_path

import time
import sys

ABPRED_DIR = Path.cwd().parent
if ABPRED_DIR not in sys.path:
    sys.path.append(str(ABPRED_DIR))
    
from AbPred.interface_contacts import InterfaceContacts
from AbPred.features_ic import ArpeggioFeatures
from AbPred.FoldX import FoldX
from features3D.Structural import run_pops
from features3D.Structural import POPS_parse2
from AbPred.FoldX import names_stability_complex_wt,names_stability_complex_mut
from AbPred.FoldX import read_analyse_complex
from AbPred.FoldX import convert_features_to_differences

import prody


/mnt/d/Python_projects/AbPred/AbPred/../libs/arpeggio


In [14]:
CWD = Path.cwd()


# PDBs dir
PDBS_DIR = Path("skempiAB/")
# Dataframe , sort to match pdbfiles order
ab_data_singleMut = pd.read_csv("../data/skempi_ABlike_singleMut.Final.csv",index_col=0)
ab_data_singleMut.sort_values('pdb_mutation',inplace=True)

# Add column with partner info
ab_data_singleMut["Partners(A_B)"] = ab_data_singleMut['#Pdb'].str.split('_',n=1,expand=True)[1]

# PDB files
pdbs_mut = list(PDBS_DIR.glob('*mut.pdb'))
pdbs_wt = list(PDBS_DIR.glob('*wt.pdb'))

# Clean structures to run arpeggio

In [39]:
TOOLS_DIR = ABPRED_DIR/"libs/tools"
CLEANPDB = TOOLS_DIR / "clean_pdb.py"

In [40]:
def run_cleanpdb(filepath,pdb):
    sys.argv = ["",pdb]
    run_path(str(filepath),run_name="__main__")

In [41]:
if pdbs_mut:
    for pdb in pdbs_mut:
        run_cleanpdb(CLEANPDB,str(pdb))

/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

...

/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Could not assign element 'M' for Atom (name=MG) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given el

/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Could not assign element 'M' for Atom (name=MG) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given el

/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'N' for Atom (name=N) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CA) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=C) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'O' for Atom (name=O) with given element ''
  warnings.warn(msg, PDBConstructionWarning)
/Users/vfica/miniconda3/envs/bio/lib/python3.6/site-packages/Bio/PDB/Atom.py:185: PDBConstructionWarning: Used element 'C' for Atom (name=CB) with given element ''
  w

In [3]:
pdbs_clean_mut = list(PDBS_DIR.glob('*mut.clean.pdb'))


In [4]:
len(pdbs_clean_mut)

728

# Get only protein data

In [5]:
for pdb in pdbs_clean_mut:
    
    parser = prody.parsePDB(pdb)
    protein = parser.select("protein")
    prody.writePDB(str(pdb)[:-10]+".protein",protein)

@> 4913 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4913 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4913 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4914 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4914 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4914 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4914 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4909 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4909 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 4835 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4828 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4835 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4834 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 4834 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4831 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4826 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4826 atoms and 1 coordinate set(s) we

@> 4721 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4716 atoms and 1 coordinate set(s) were parsed in 0.08s.
@> 4719 atoms and 1 coordinate set(s) were parsed in 0.11s.
@> 4716 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.09s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 4720 atoms and 1 coordinate set(s) were parsed in 0.07s.
@> 4718 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4723 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4721 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4718 atoms and 1 coordinate set(s) were parsed in 0.07s.
@> 4716 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4723 atoms and 1 coordinate set(s) were parsed in 0.08s.
@> 4721 atoms and 1 coordinate set(s) were parsed in 0.12s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.07s.
@> 4718 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 4718 atoms and 1 coordinate set(s) we

@> 4248 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4245 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4244 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4246 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 4252 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4249 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4248 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4238 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 4241 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4241 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4240 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4248 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 8021 atoms and 1 coordinate set(s) were parsed in 0.08s.
@> 8021 atoms and 1 coordinate set(s) were parsed in 0.08s.
@> 8022 atoms and 1 coordinate set(s) were parsed in 0.09s.
@> 8018 atoms and 1 coordinate set(s) were parsed in 0.17s.
@> 8016 atoms and 1 coordinate set(s) we

@> 5341 atoms and 1 coordinate set(s) were parsed in 0.08s.
@> 5340 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 5339 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 5056 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 5056 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 5056 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 5056 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 5055 atoms and 1 coordinate set(s) were parsed in 0.08s.
@> 5053 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 5053 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 5053 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 5054 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 5056 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 5056 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 5055 atoms and 1 coordinate set(s) were parsed in 0.09s.
@> 5056 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 5056 atoms and 1 coordinate set(s) we

@> 6036 atoms and 1 coordinate set(s) were parsed in 0.08s.
@> 6037 atoms and 1 coordinate set(s) were parsed in 0.07s.
@> 6041 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 6035 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 6035 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 6033 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 6036 atoms and 1 coordinate set(s) were parsed in 0.08s.
@> 6033 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 6037 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 6033 atoms and 1 coordinate set(s) were parsed in 0.16s.
@> 6038 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 6037 atoms and 1 coordinate set(s) were parsed in 0.07s.
@> 6044 atoms and 1 coordinate set(s) were parsed in 0.07s.
@> 6032 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 6039 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 6037 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 6039 atoms and 1 coordinate set(s) we

@> 2513 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 2510 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 5335 atoms and 1 coordinate set(s) were parsed in 0.10s.
@> 5332 atoms and 1 coordinate set(s) were parsed in 0.07s.
@> 5032 atoms and 1 coordinate set(s) were parsed in 0.10s.
@> 14816 atoms and 1 coordinate set(s) were parsed in 0.31s.
@> 14816 atoms and 1 coordinate set(s) were parsed in 0.34s.
@> 14820 atoms and 1 coordinate set(s) were parsed in 0.31s.
@> 14818 atoms and 1 coordinate set(s) were parsed in 0.33s.
@> 14814 atoms and 1 coordinate set(s) were parsed in 0.17s.
@> 14813 atoms and 1 coordinate set(s) were parsed in 0.33s.
@> 14818 atoms and 1 coordinate set(s) were parsed in 0.46s.
@> 14817 atoms and 1 coordinate set(s) were parsed in 0.22s.
@> 14820 atoms and 1 coordinate set(s) were parsed in 0.16s.
@> 4580 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4580 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4579 atoms and 1 coordinate 

In [13]:
pdbs_protein_mut = list(PDBS_DIR.glob('*mut.protein.pdb'))
len(pdbs_protein_mut)

728

In [27]:
for pdb in pdbs_wt:
    
    parser = prody.parsePDB(pdb)
    protein = parser.select("protein")
    prody.writePDB(str(pdb)[:-4]+".protein",protein)

@> 4916 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4916 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4916 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4916 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4916 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4916 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4916 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4916 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4916 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4833 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4833 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4833 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4833 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4833 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4833 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4833 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4833 atoms and 1 coordinate set(s) we

@> 4717 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4717 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 4717 atoms and 1 coordinate set(s) we

@> 4245 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4245 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 4245 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4249 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 4249 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 4249 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4249 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 4244 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 4244 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 4244 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4244 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 4250 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 8019 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 8019 atoms and 1 coordinate set(s) were parsed in 0.09s.
@> 8019 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 8019 atoms and 1 coordinate set(s) were parsed in 0.11s.
@> 8019 atoms and 1 coordinate set(s) we

@> 5339 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 5339 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 5340 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 5059 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 5059 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 5059 atoms and 1 coordinate set(s) were parsed in 0.07s.
@> 5059 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 5059 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 5059 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 5059 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 5059 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 5059 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 5059 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 5059 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 5059 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 5059 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 5059 atoms and 1 coordinate set(s) we

@> 6039 atoms and 1 coordinate set(s) were parsed in 0.07s.
@> 6039 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 6039 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 6039 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 6039 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 6039 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 6039 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 6039 atoms and 1 coordinate set(s) were parsed in 0.08s.
@> 6039 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 6039 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 6039 atoms and 1 coordinate set(s) were parsed in 0.11s.
@> 6039 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 6039 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 6039 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 6039 atoms and 1 coordinate set(s) were parsed in 0.07s.
@> 6039 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 6039 atoms and 1 coordinate set(s) we

@> 2516 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 2516 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 5338 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 5338 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 5036 atoms and 1 coordinate set(s) were parsed in 0.06s.
@> 14816 atoms and 1 coordinate set(s) were parsed in 0.13s.
@> 14816 atoms and 1 coordinate set(s) were parsed in 0.16s.
@> 14816 atoms and 1 coordinate set(s) were parsed in 0.14s.
@> 14816 atoms and 1 coordinate set(s) were parsed in 0.12s.
@> 14816 atoms and 1 coordinate set(s) were parsed in 0.13s.
@> 14816 atoms and 1 coordinate set(s) were parsed in 0.19s.
@> 14816 atoms and 1 coordinate set(s) were parsed in 0.16s.
@> 14816 atoms and 1 coordinate set(s) were parsed in 0.12s.
@> 14816 atoms and 1 coordinate set(s) were parsed in 0.14s.
@> 4583 atoms and 1 coordinate set(s) were parsed in 0.05s.
@> 4583 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 4583 atoms and 1 coordinate 

In [12]:
pdbs_protein_wt = list(PDBS_DIR.glob('*wt.protein.pdb'))
len(pdbs_protein_wt)

728

# Calcule contact data mutant

In [39]:
def main(i,pdbfile):
    
    partners_pdbs = ab_data_singleMut["Partners(A_B)"].iloc[i]
    ic = InterfaceContacts(pdbfile)
    print("### Running arpeggio ###")
    print("Getting contact on ", pdbfile.name)
    ic.run_arpeggio()
    time.sleep(10)
    ic.get_ic(partners=partners_pdbs)
    print("Finish getting interface contact\n")
    #ic.get_pymol_contacts()
    print("### END ###\n")

In [19]:
# not parallelized
for i,pdb in enumerate(pdbs_protein_mut[80:],80):
    main(i,pdb)

### Running arpeggio ###
Getting contact on  1JRH_Repair-KI42A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1JRH_Repair-KI42M-mut.protein.pdb


KeyboardInterrupt: 

In [40]:
with Pool(10) as p:
    print(p.starmap(main, enumerate(pdbs_protein_mut[67:],67)))

### Running arpeggio ###
### Running arpeggio ###
### Running arpeggio ###
### Running arpeggio ###
### Running arpeggio ###
### Running arpeggio ###
### Running arpeggio ###
### Running arpeggio ###
Getting contact on  1MHP_Repair-GH100M-mut.protein.pdb
Getting contact on  1JRH_Repair-NI38Q-mut.protein.pdb
Getting contact on  1MHP_Repair-NL51E-mut.protein.pdb
### Running arpeggio ###
Getting contact on  1JRH_Repair-DH56A-mut.protein.pdb
Getting contact on  1JRH_Repair-WL92A-mut.protein.pdb
### Running arpeggio ###
Getting contact on  1MHP_Repair-HL30K-mut.protein.pdb
Getting contact on  1MHP_Repair-SL90W-mut.protein.pdb
Getting contact on  1MLC_Repair-SB57V-mut.protein.pdb
Getting contact on  1N8Z_Repair-YB109V-mut.protein.pdb
Getting contact on  1VFB_Repair-DB58N-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1VFB_Repair-DC119A-mut.protein.pdb
Getting only interface contacts
Finish getting in

Getting contact on  1JRH_Repair-EI45P-mut.protein.pdb
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1JRH_Repair-SL93A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1VFB_Repair-HA30A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1MHP_Repair-KH64N-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1MHP_Repair-GH53N-mut.protein.pdb
Getting only interface contacts
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1MHP_Repair-TH50Q-mut.protein.pdb
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1MHP_Repair-RH31Q-mut.protein.pdb
Getting only interface contact

Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1JRH_Repair-WI46F-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1JRH_Repair-KI37M-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1VFB_Repair-NB56A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1MHP_Repair-YH58W-mut.protein.pdb
Getting only interface contacts
Getting only interface contacts
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1MHP_Repair-SH52T-mut.protein.pdb
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1MHP_Repair-LL48W-mut.protein.pdb
Finish getting inter

Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1VFB_Repair-DB100A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1XGQ_Repair-VB33L-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1N8Z_Repair-RB59A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1MLC_Repair-NA92A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1VFB_Repair-SA93A-mut.protein.pdb
Getting only interface contacts
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1MHP_Repair-NL29Y-mut.protein.pdb
Finish getting inte

Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1VFB_Repair-YB32A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  2JEL_Repair-PP11E-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  2JEL_Repair-EP75R-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  2JEL_Repair-TP7S-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  2BDN_Repair-NH28Q-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  1VFB_Repair-TA53R-mut.protein.pdb
Getting only interface contacts
Finish getting interf

...

Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  2NZ9_Repair-IA928A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3HFM_Repair-YH53A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3HFM_Repair-LY75A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3HFM_Repair-DY101K-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3HFM_Repair-YL96A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3N85_Repair-SH50G-mut.protein.pdb
Getting only interface contacts
Finish getting int

Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3NPS_Repair-TA93A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3LZF_Repair-DA222G-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3N85_Repair-WH30R-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3SE8_Repair-PH78A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3NGB_Repair-PH63K-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3NPS_Repair-HA138A-mut.protein.pdb
Getting only interface contacts
Finish getting int

Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  2NYY_Repair-TA1035A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3SE9_Repair-FL91A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3NGB_Repair-YL26A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3SE8_Repair-EL91A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3NPS_Repair-QA168A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3NGB_Repair-FL89A-mut.protein.pdb
Getting only interface contacts
Finish getting in

Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3SE9_Repair-GL29A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3SE9_Repair-VL3A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  5C6T_Repair-NH97A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3SE8_Repair-WH55A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  4JPK_Repair-TA35S-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3SE9_Rep

Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  4I77_Repair-YH103F-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3W2D_Repair-YA45E-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  5C6T_Repair-YH98A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  4I77_Repair-YL32A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  4ZS6_Repair-EA156A-mut.protein.pdb
Getting only interface contacts
Finish getting interface contact

### END ###

### Running arpeggio ###
Getting contact on  3W2D_Repair-YA45F-mut.protein.pdb
Getting only interface contacts
Finish getting int

# Extract contact features 

In [81]:
ic_files = list(PDBS_DIR.glob("*.interface_contacts"))

In [84]:
PDBS_DIR

PosixPath('skempiAB')

In [42]:
features = np.empty((len(pdbs_protein_mut),15))
for i,(ic,pdb) in enumerate(zip(ic_files,pdbs_protein_mut)):
    print(ic,pdb)
    ic_features = ArpeggioFeatures(level_sift="normal")
    ic_features.parse_contactdata(icfile=ic)
    ic_features.parse_pdbdata(pdbfile=pdb)
    
    contacts = ic_features.get_features()
    
    
    features[i] = contacts

skempiAB/1AHW_Repair-DC167A-mut.protein.interface_contacts skempiAB/1AHW_Repair-DC167A-mut.protein.pdb
skempiAB/1AHW_Repair-LC165A-mut.protein.interface_contacts skempiAB/1AHW_Repair-LC165A-mut.protein.pdb
skempiAB/1AHW_Repair-NC188A-mut.protein.interface_contacts skempiAB/1AHW_Repair-NC188A-mut.protein.pdb
skempiAB/1AHW_Repair-TC156A-mut.protein.interface_contacts skempiAB/1AHW_Repair-TC156A-mut.protein.pdb
skempiAB/1AHW_Repair-TC159A-mut.protein.interface_contacts skempiAB/1AHW_Repair-TC159A-mut.protein.pdb
skempiAB/1AHW_Repair-TC186A-mut.protein.interface_contacts skempiAB/1AHW_Repair-TC186A-mut.protein.pdb
skempiAB/1AHW_Repair-VC187A-mut.protein.interface_contacts skempiAB/1AHW_Repair-VC187A-mut.protein.pdb
skempiAB/1AHW_Repair-YC145A-mut.protein.interface_contacts skempiAB/1AHW_Repair-YC145A-mut.protein.pdb
skempiAB/1AHW_Repair-YC146A-mut.protein.interface_contacts skempiAB/1AHW_Repair-YC146A-mut.protein.pdb
skempiAB/1BJ1_Repair-HH101Y-mut.protein.interface_contacts skempiAB/1BJ1_

skempiAB/1JRH_Repair-KI88A-mut.protein.interface_contacts skempiAB/1JRH_Repair-KI88A-mut.protein.pdb
skempiAB/1JRH_Repair-NI38A-mut.protein.interface_contacts skempiAB/1JRH_Repair-NI38A-mut.protein.pdb
skempiAB/1JRH_Repair-NI38Q-mut.protein.interface_contacts skempiAB/1JRH_Repair-NI38Q-mut.protein.pdb
skempiAB/1JRH_Repair-NI43A-mut.protein.interface_contacts skempiAB/1JRH_Repair-NI43A-mut.protein.pdb
skempiAB/1JRH_Repair-NI69A-mut.protein.interface_contacts skempiAB/1JRH_Repair-NI69A-mut.protein.pdb
skempiAB/1JRH_Repair-RH100A-mut.protein.interface_contacts skempiAB/1JRH_Repair-RH100A-mut.protein.pdb
skempiAB/1JRH_Repair-RI74A-mut.protein.interface_contacts skempiAB/1JRH_Repair-RI74A-mut.protein.pdb
skempiAB/1JRH_Repair-SI44A-mut.protein.interface_contacts skempiAB/1JRH_Repair-SI44A-mut.protein.pdb
skempiAB/1JRH_Repair-SL93A-mut.protein.interface_contacts skempiAB/1JRH_Repair-SL93A-mut.protein.pdb
skempiAB/1JRH_Repair-TI4V-mut.protein.interface_contacts skempiAB/1JRH_Repair-TI4V-mut.pr

skempiAB/1MHP_Repair-SL27Q-mut.protein.interface_contacts skempiAB/1MHP_Repair-SL27Q-mut.protein.pdb
skempiAB/1MHP_Repair-SL90K-mut.protein.interface_contacts skempiAB/1MHP_Repair-SL90K-mut.protein.pdb
skempiAB/1MHP_Repair-SL90Q-mut.protein.interface_contacts skempiAB/1MHP_Repair-SL90Q-mut.protein.pdb
skempiAB/1MHP_Repair-SL90R-mut.protein.interface_contacts skempiAB/1MHP_Repair-SL90R-mut.protein.pdb
skempiAB/1MHP_Repair-SL90T-mut.protein.interface_contacts skempiAB/1MHP_Repair-SL90T-mut.protein.pdb
skempiAB/1MHP_Repair-SL90W-mut.protein.interface_contacts skempiAB/1MHP_Repair-SL90W-mut.protein.pdb
skempiAB/1MHP_Repair-TH33N-mut.protein.interface_contacts skempiAB/1MHP_Repair-TH33N-mut.protein.pdb
skempiAB/1MHP_Repair-TH33Q-mut.protein.interface_contacts skempiAB/1MHP_Repair-TH33Q-mut.protein.pdb
skempiAB/1MHP_Repair-TH33V-mut.protein.interface_contacts skempiAB/1MHP_Repair-TH33V-mut.protein.pdb
skempiAB/1MHP_Repair-TH50E-mut.protein.interface_contacts skempiAB/1MHP_Repair-TH50E-mut.pr

skempiAB/1VFB_Repair-SC24A-mut.protein.interface_contacts skempiAB/1VFB_Repair-SC24A-mut.protein.pdb
skempiAB/1VFB_Repair-TA52F-mut.protein.interface_contacts skempiAB/1VFB_Repair-TA52F-mut.protein.pdb
skempiAB/1VFB_Repair-TA53R-mut.protein.interface_contacts skempiAB/1VFB_Repair-TA53R-mut.protein.pdb
skempiAB/1VFB_Repair-TB30A-mut.protein.interface_contacts skempiAB/1VFB_Repair-TB30A-mut.protein.pdb
skempiAB/1VFB_Repair-TC118A-mut.protein.interface_contacts skempiAB/1VFB_Repair-TC118A-mut.protein.pdb
skempiAB/1VFB_Repair-VC120A-mut.protein.interface_contacts skempiAB/1VFB_Repair-VC120A-mut.protein.pdb
skempiAB/1VFB_Repair-WA92A-mut.protein.interface_contacts skempiAB/1VFB_Repair-WA92A-mut.protein.pdb
skempiAB/1VFB_Repair-WB52A-mut.protein.interface_contacts skempiAB/1VFB_Repair-WB52A-mut.protein.pdb
skempiAB/1VFB_Repair-YA32A-mut.protein.interface_contacts skempiAB/1VFB_Repair-YA32A-mut.protein.pdb
skempiAB/1VFB_Repair-YA32W-mut.protein.interface_contacts skempiAB/1VFB_Repair-YA32W-mu

skempiAB/2JEL_Repair-EP85K-mut.protein.interface_contacts skempiAB/2JEL_Repair-EP85K-mut.protein.pdb
skempiAB/2JEL_Repair-EP85Q-mut.protein.interface_contacts skempiAB/2JEL_Repair-EP85Q-mut.protein.pdb
skempiAB/2JEL_Repair-FP2W-mut.protein.interface_contacts skempiAB/2JEL_Repair-FP2W-mut.protein.pdb
skempiAB/2JEL_Repair-FP2Y-mut.protein.interface_contacts skempiAB/2JEL_Repair-FP2Y-mut.protein.pdb
skempiAB/2JEL_Repair-HP76A-mut.protein.interface_contacts skempiAB/2JEL_Repair-HP76A-mut.protein.pdb
skempiAB/2JEL_Repair-HP76D-mut.protein.interface_contacts skempiAB/2JEL_Repair-HP76D-mut.protein.pdb
skempiAB/2JEL_Repair-KP24E-mut.protein.interface_contacts skempiAB/2JEL_Repair-KP24E-mut.protein.pdb
skempiAB/2JEL_Repair-KP27E-mut.protein.interface_contacts skempiAB/2JEL_Repair-KP27E-mut.protein.pdb
skempiAB/2JEL_Repair-KP72E-mut.protein.interface_contacts skempiAB/2JEL_Repair-KP72E-mut.protein.pdb
skempiAB/2JEL_Repair-KP72R-mut.protein.interface_contacts skempiAB/2JEL_Repair-KP72R-mut.protei

skempiAB/2VIR_Repair-SC115L-mut.protein.interface_contacts skempiAB/2VIR_Repair-SC115L-mut.protein.pdb
skempiAB/2VIR_Repair-TC89I-mut.protein.interface_contacts skempiAB/2VIR_Repair-TC89I-mut.protein.pdb
skempiAB/2VIS_Repair-IC89T-mut.protein.interface_contacts skempiAB/2VIS_Repair-IC89T-mut.protein.pdb
skempiAB/3BN9_Repair-DB214A-mut.protein.interface_contacts skempiAB/3BN9_Repair-DB214A-mut.protein.pdb
skempiAB/3BN9_Repair-DB46A-mut.protein.interface_contacts skempiAB/3BN9_Repair-DB46A-mut.protein.pdb
skempiAB/3BN9_Repair-DB47A-mut.protein.interface_contacts skempiAB/3BN9_Repair-DB47A-mut.protein.pdb
skempiAB/3BN9_Repair-DB91A-mut.protein.interface_contacts skempiAB/3BN9_Repair-DB91A-mut.protein.pdb
skempiAB/3BN9_Repair-EB163A-mut.protein.interface_contacts skempiAB/3BN9_Repair-EB163A-mut.protein.pdb
skempiAB/3BN9_Repair-FB50A-mut.protein.interface_contacts skempiAB/3BN9_Repair-FB50A-mut.protein.pdb
skempiAB/3BN9_Repair-FB89A-mut.protein.interface_contacts skempiAB/3BN9_Repair-FB89A-

skempiAB/3HFM_Repair-RY21Q-mut.protein.interface_contacts skempiAB/3HFM_Repair-RY21Q-mut.protein.pdb
skempiAB/3HFM_Repair-RY21W-mut.protein.interface_contacts skempiAB/3HFM_Repair-RY21W-mut.protein.pdb
skempiAB/3HFM_Repair-RY73A-mut.protein.interface_contacts skempiAB/3HFM_Repair-RY73A-mut.protein.pdb
skempiAB/3HFM_Repair-SH31A-mut.protein.interface_contacts skempiAB/3HFM_Repair-SH31A-mut.protein.pdb
skempiAB/3HFM_Repair-SY100A-mut.protein.interface_contacts skempiAB/3HFM_Repair-SY100A-mut.protein.pdb
skempiAB/3HFM_Repair-TY89A-mut.protein.interface_contacts skempiAB/3HFM_Repair-TY89A-mut.protein.pdb
skempiAB/3HFM_Repair-WH98A-mut.protein.interface_contacts skempiAB/3HFM_Repair-WH98A-mut.protein.pdb
skempiAB/3HFM_Repair-WH98F-mut.protein.interface_contacts skempiAB/3HFM_Repair-WH98F-mut.protein.pdb
skempiAB/3HFM_Repair-WY63A-mut.protein.interface_contacts skempiAB/3HFM_Repair-WY63A-mut.protein.pdb
skempiAB/3HFM_Repair-YH33A-mut.protein.interface_contacts skempiAB/3HFM_Repair-YH33A-mut.

skempiAB/3NGB_Repair-YL26A-mut.protein.interface_contacts skempiAB/3NGB_Repair-YL26A-mut.protein.pdb
skempiAB/3NGB_Repair-YL26S-mut.protein.interface_contacts skempiAB/3NGB_Repair-YL26S-mut.protein.pdb
skempiAB/3NGB_Repair-YL87A-mut.protein.interface_contacts skempiAB/3NGB_Repair-YL87A-mut.protein.pdb
skempiAB/3NPS_Repair-DA214A-mut.protein.interface_contacts skempiAB/3NPS_Repair-DA214A-mut.protein.pdb
skempiAB/3NPS_Repair-DA46A-mut.protein.interface_contacts skempiAB/3NPS_Repair-DA46A-mut.protein.pdb
skempiAB/3NPS_Repair-DA47A-mut.protein.interface_contacts skempiAB/3NPS_Repair-DA47A-mut.protein.pdb
skempiAB/3NPS_Repair-DA91A-mut.protein.interface_contacts skempiAB/3NPS_Repair-DA91A-mut.protein.pdb
skempiAB/3NPS_Repair-EA163A-mut.protein.interface_contacts skempiAB/3NPS_Repair-EA163A-mut.protein.pdb
skempiAB/3NPS_Repair-FA50A-mut.protein.interface_contacts skempiAB/3NPS_Repair-FA50A-mut.protein.pdb
skempiAB/3NPS_Repair-FA89A-mut.protein.interface_contacts skempiAB/3NPS_Repair-FA89A-mu

skempiAB/3SE9_Repair-YH104A-mut.protein.interface_contacts skempiAB/3SE9_Repair-YH104A-mut.protein.pdb
skempiAB/3SE9_Repair-YL28A-mut.protein.interface_contacts skempiAB/3SE9_Repair-YL28A-mut.protein.pdb
skempiAB/3W2D_Repair-KA67N-mut.protein.interface_contacts skempiAB/3W2D_Repair-KA67N-mut.protein.pdb
skempiAB/3W2D_Repair-KA67Q-mut.protein.interface_contacts skempiAB/3W2D_Repair-KA67Q-mut.protein.pdb
skempiAB/3W2D_Repair-KA67R-mut.protein.interface_contacts skempiAB/3W2D_Repair-KA67R-mut.protein.pdb
skempiAB/3W2D_Repair-YA45E-mut.protein.interface_contacts skempiAB/3W2D_Repair-YA45E-mut.protein.pdb
skempiAB/3W2D_Repair-YA45F-mut.protein.interface_contacts skempiAB/3W2D_Repair-YA45F-mut.protein.pdb
skempiAB/3W2D_Repair-YA45L-mut.protein.interface_contacts skempiAB/3W2D_Repair-YA45L-mut.protein.pdb
skempiAB/4GXU_Repair-DA189E-mut.protein.interface_contacts skempiAB/4GXU_Repair-DA189E-mut.protein.pdb
skempiAB/4GXU_Repair-DA224G-mut.protein.interface_contacts skempiAB/4GXU_Repair-DA224G-

In [43]:
features15 = ['clash', 'covalent', 'vdw_clash', 'vdw', 'proximal', 'hbond', 'weak_hbond', 'xbond', 'ionic',
              'metal_complex', 'aromatic', 'hydrophobic', 'carbonyl', 'polar', 'weak_polar']

In [44]:
DF_contact15_mut = pd.DataFrame(features, index=[pdb.name for pdb in pdbs_protein_mut],columns=features15)

In [45]:
# Check contact data if are all empty
(DF_contact15_mut.mean(axis=1) == 0).value_counts()

False    728
dtype: int64

In [47]:
DF_contact15_mut.to_csv('../data/DF_contact15_mut_skempiAB.csv')

# Energetic features 


In [13]:
energetic_featuresMUT = np.empty((len(pdbs_protein_mut),29))

try:
    os.chdir(PDBS_DIR)
    
    for i,pdb in enumerate(pdbs_protein_mut):
        partners = ab_data_singleMut["Partners(A_B)"].iloc[i]
        foldx = FoldX(verbose=False)
        result_analyse = foldx.analyse_complex(pdb_file=pdb.name, partners=partners)
        energetic_featuresMUT[i] = result_analyse
finally:
    os.chdir(CWD)


foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin 

foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin 

foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin 

In [18]:
energetic_dataMUT = pd.DataFrame(energetic_featuresMUT, index=[pdb.name for pdb in pdbs_protein_mut],columns=names_stability_complex_mut)

In [20]:
energetic_dataMUT.to_csv("../data/DF_energetic_mut_skempiAB.csv")

# WT energetic 

In [39]:
# I have to run twice this, for an error in the first run

PosixPath('skempiAB/3BN9_Repair-RB82A-wt.protein.pdb')

In [44]:
energetic_featuresWT = np.empty((len(pdbs_protein_wt),29))

try:
    os.chdir(PDBS_DIR)
    
    for i,pdb in enumerate(pdbs_protein_wt[437:],437):
        partners = ab_data_singleMut["Partners(A_B)"].iloc[i]
        foldx = FoldX(verbose=False)
        result_analyse = foldx.analyse_complex(pdb_file=pdb.name, partners=partners)
        energetic_featuresWT[i] = result_analyse
finally:
    os.chdir(CWD)

foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin 

foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin folder already in PATH
foldx bin 

In [68]:
# Get interaction files for wt 

interaction_files = list()
wt_fxout_files = list(PDBS_DIR.glob("*wt.protein_AC.fxout"))
for f in wt_fxout_files:
    fname = f.name
    if fname.startswith("Interaction_"):
        interaction_files.append(f)

In [71]:
# read interaction data
energetic_featuresWT = np.empty((len(pdbs_protein_wt),29))
for i,f in enumerate(interaction_files):
    result_analyse = read_analyse_complex(f)
    energetic_featuresWT[i] = result_analyse

In [75]:
energetic_dataWT = pd.DataFrame(energetic_featuresWT, index=[pdb.name for pdb in pdbs_protein_wt],columns=names_stability_complex_wt)

In [78]:
energetic_dataWT.to_csv("../data/DF_energetic_wt_skempiAB.csv")

### Join energetic data

In [3]:
DF_energetic_wt = pd.read_csv("../data/DF_energetic_wt_skempiAB.csv",index_col=0)
DF_energetic_mut = pd.read_csv("../data/DF_energetic_mut_skempiAB.csv",index_col=0)

In [4]:
DF_energetic_mut.reset_index(inplace=True)
DF_energetic_wt.reset_index(inplace=True)


In [5]:
pdb_names_mut = DF_energetic_mut["index"].str.rsplit("-",n=1,expand=True)[0]
DF_energetic_mut["names"] = pdb_names_mut

In [6]:
pdb_names_wt = DF_energetic_wt["index"].str.rsplit("-",n=1,expand=True)[0]
DF_energetic_wt["names"] = pdb_names_wt

In [7]:
DF_energetic_wt.set_index("names",inplace=True)
DF_energetic_mut.set_index("names",inplace=True)


In [8]:
# merge
DF_energetic_wt_mut = DF_energetic_mut.merge(DF_energetic_wt,on='names')

In [9]:
DF_energetic_changes =  convert_features_to_differences(DF_energetic_wt_mut)

In [10]:
DF_energetic_changes.to_csv("../data/DF_energetic_wt_mut_skempiAB.csv")

# SASA features

In [11]:
def get_pdb_chain(pdb,partner,outdir):
    protein = prody.parsePDB(pdb,chain=partner)
    pdbwrited = prody.writePDB(str(outdir.resolve())+"/"+"%s_%s" % (pdb.name[:-4], partner), protein)
    print("writing %s_%s" % (pdb.name[:-4], partner))
    return pdbwrited

In [16]:
# MUtant interface sasas calculate as (TA + TB - T) / 2.0.
# When T=total sas complex, TA= total sasa partner A , TB=total sasa partner B.

outfolder = Path('popout_skempi')
if not outfolder.exists():
    outfolder.mkdir()
complexMUT_sasas = list()
partnerA_MUT_sasas = list()
partnerB_MUT_sasas = list()
for i,pdb in enumerate(pdbs_protein_mut):
    
    pp = ab_data_singleMut["Partners(A_B)"].iloc[i]
    
    # Calculate sasa for complex
    asa_data = run_pops(str(pdb.resolve()), outdir=outfolder, mode='total')
    pops_complex = POPS_parse2(asa_data, mode='total') 
    complexMUT_sasas.append(list(pops_complex.values()))
    
    # Calculate sasa for partner A
    pdbA = get_pdb_chain(pdb.resolve(),partner=pp.split("_")[0],outdir=outfolder)
    asa_data = run_pops(pdbA, outdir=outfolder, mode='total')
    pops_A = POPS_parse2(asa_data, mode='total') 
    partnerA_MUT_sasas.append(list(pops_A.values()))
    
    # Calculate sasa for partner B
    pdbB = get_pdb_chain(pdb.resolve(),partner=pp.split("_")[1],outdir=outfolder)
    asa_data = run_pops(pdbB, outdir=outfolder, mode='total')
    pops_B = POPS_parse2(asa_data, mode='total') 
    partnerB_MUT_sasas.append(list(pops_B.values()))

@> 3304 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 1609 atoms and 1 coordinate set(s) were parsed in 0.02s.


writing 1AHW_Repair-DC167A-mut.protein_AB
writing 1AHW_Repair-DC167A-mut.protein_C


@> 3304 atoms and 1 coordinate set(s) were parsed in 0.03s.
@> 1609 atoms and 1 coordinate set(s) were parsed in 0.02s.


writing 1AHW_Repair-LC165A-mut.protein_AB
writing 1AHW_Repair-LC165A-mut.protein_C


@> 3304 atoms and 1 coordinate set(s) were parsed in 0.03s.


...

writing 5DWU_Repair-IB169A-mut.protein_HL
writing 5DWU_Repair-IB169A-mut.protein_AB


@> 3105 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 2758 atoms and 1 coordinate set(s) were parsed in 0.04s.


writing 5DWU_Repair-IB84A-mut.protein_HL
writing 5DWU_Repair-IB84A-mut.protein_AB


@> 3105 atoms and 1 coordinate set(s) were parsed in 0.04s.
@> 2757 atoms and 1 coordinate set(s) were parsed in 0.03s.


writing 5DWU_Repair-QB85A-mut.protein_HL
writing 5DWU_Repair-QB85A-mut.protein_AB


In [18]:
# To numpy arrays
complexMUT_sasas = np.asarray(complexMUT_sasas)
partnerA_MUT_sasas = np.asarray(partnerA_MUT_sasas)
partnerB_MUT_sasas = np.asarray(partnerB_MUT_sasas)

In [19]:
# interface sasa complex wt  (Phil, Phob, Total)
interface_asa_MUT = ((partnerA_MUT_sasas + partnerB_MUT_sasas) - complexMUT_sasas)/2

In [23]:
interface_asa_MUT_df = pd.DataFrame(interface_asa_MUT,columns=["if_phil","if_phob","if_total"],index= pdb_names_mut)

In [25]:
interface_asa_MUT_df["sasa_phil_mut"] = complexMUT_sasas.T[0]
interface_asa_MUT_df["sasa_phob_mut"] = complexMUT_sasas.T[1]
interface_asa_MUT_df["sasa_total_mut"] = complexMUT_sasas.T[2]

In [29]:
interface_asa_MUT_df.to_csv("../data/DF_sasa_skempiAB_mut.csv")

### sasa wildtype

In [28]:

outfolder = Path('popout_skempi')
if not outfolder.exists():
    outfolder.mkdir()
complexWT_sasas = list()
for pdb in pdbs_protein_wt:
        
    # Calculate sasa for complex
    asa_data = run_pops(str(pdb.resolve()), outdir=outfolder, mode='total')
    pops_complex = POPS_parse2(asa_data, mode='total') 
    complexWT_sasas.append(list(pops_complex.values()))

In [31]:
complexWT_sasas = np.asarray(complexWT_sasas)

In [32]:
sasa_WT_df = pd.DataFrame(complexWT_sasas,columns=["sasa_phil_wt","sasa_phob_wt","sasa_wt"],index=pdb_names_wt)

## merge sasa wt mut

In [35]:
interface_asa_MUT_df.index.name = None

In [37]:
sasa_WT_df.index.name = None

In [47]:
DF_sasa_wt_mut = interface_asa_MUT_df.join(sasa_WT_df)

In [49]:
DF_sasa_wt_mut.to_csv("../data/DF_sasa_skempiAB_mut_wt.csv")

# Data Final

In [61]:
DF_contact15_mut = pd.read_csv('../data/DF_contact15_mut_skempiAB.csv',index_col=0)
DF_energetic_changes = pd.read_csv("../data/DF_energetic_wt_mut_skempiAB.csv",index_col=0)
DF_sasa_wt_mut = pd.read_csv("../data/DF_sasa_skempiAB_mut_wt.csv",index_col=0)

In [62]:
# Process
# Drop useless columns, set new index
DF_energetic_changes.drop(["index_y","index_x",'number_of_residues_y',"number_of_residues_x"],axis=1,inplace=True)
DF_energetic_changes.index.name = None

In [65]:
DF_contact15_mut.index = DF_energetic_changes.index

In [69]:
DF_contact_energy_sasa = DF_contact15_mut.join([DF_energetic_changes,DF_sasa_wt_mut])

In [79]:
# add experimental ddG
DF_contact_energy_sasa["ddG_exp"] =  ab_data_singleMut["ddG"].values

In [80]:
DF_contact_energy_sasa.to_csv("../data/DF_contact15_energy_sasa.skempiAB.csv")